## DEMO - BALANCES DE ENERGÍA AUTOMATIZADOS

### INTRODUCCION

La automatización de procesos manuales es clave para mejorar la precisión y reducir el tiempo necesario para el análisis y la toma de decisiones. En esta demo, presentaremos una solución automatizada para la gestión de balances de energía, que integra varias fuentes de datos y utiliza herramientas avanzadas para transformar, analizar y cargar la información.

####Fuentes para la Extracción

- Excel enviado por las centrales de energía 
- API SIMEM, Plan despacho de energía por unidad de centrales
- API SIMEM, precios de la energía

#### Transformación

- Cambio de formato de Excel a SQL
- Cambio de formato de JSON a SQL
- Data Quality a bases de datos
- Comparación bases de datos

#### Carga

- Enviar Balance de energía


##Instalación de librerías


Se instalan algunas librerías necesarias para trabajar con archivos de excel que facilitan leer y escribir este tipo de archivos de manera automática.También se instala Request, que es una librería útil para hacer conexiones a internet y Azure-storage-blob para conectar y manejar el archivo de excel enviado por las centrales, este fue guardado en esta herramienta de almacenamiento.

In [0]:
%sh
pip install openpyxl xlrd requests azure-storage-blob


[notice] A new release of pip available: 22.2.2 -> 24.2
[notice] To update, run: pip install --upgrade pip


##Requisitos

En el siguiente bloque de código estamos estableciendo el entorno necesario para nuestro pipeline. Primero, importamos todas las funciones de PySpark SQL para manejar operaciones sobre los datos de manera distribuida. también incluimos la librería requests para hacer llamadas a APIs externas y manipular las respuestas en formato JSON. Usamos pandas para la lectura inicial de la data desde el archivo de excel para posteriormente llevarlo a un dataframe

También estamos conectándonos a un contenedor de Azure Blob Storage con BlobServiceClient, lo cual nos permite interactuar con los datos almacenados en la nube. Finalmente, inicializamos una sesión de Spark que será el motor principal para procesar los datos de manera distribuida, facilitando el manejo de grandes volúmenes de información de manera eficiente.

In [0]:
# De pyspark sql functions importeme todas las funciones disponibles
from pyspark.sql.functions import *

#Importo la libreria requests de python para utilizarla en el llamado a la api
import requests
import json

#Importo pandas para trabajar con mi dataframe
import pandas as pd

#Importo desde la libreria de azure-storage-blob un BlobServiceClient para poder manipular un blob storage
from azure.storage.blob import BlobServiceClient


from pyspark.sql import SparkSession
#Creando la sesion de spark
spark = SparkSession.builder.appName("Reading_excel_tables").getOrCreate()

#Extracción

Ya empezamos el proceso de extracción de dato.

Aquí estoy configurando las credenciales y la información necesaria para conectarme a un contenedor en Azure Blob Storage y acceder al archivo de Excel. Defino el nombre de la cuenta de almacenamiento (eontec), el contenedor (despachogeneradora), y el archivo (DespachoGeneradoraX.xlsx) que necesito procesar. Uso una clave de acceso (access_key) para autenticarme y obtener permisos para interactuar con los datos.

Es importante destacar que aunque esta clave es visible en el demo, en un entorno de producción nunca se debería exponer este tipo de información sensible directamente en el código. La mejor práctica sería almacenar estas credenciales en un sistema seguro como Azure Key Vault para evitar riesgos de seguridad
o haciendo uso de la funcionalidad de secrets de Databrick

In [0]:
"""
    Aqui estoy asignando la informacion que identifica mi storage account de azure donde se encuentra almacenado mi 
    archivo de excel dentro de mi contenedor

    - storage_account -> eontec
    - container_name -> despachogeneradora
    - blob_name (nombre de mi blob) -> "DespachoGeneradoraX.xlsx"
    - access_key (llave de acceso para poder acceder "ver" el contenido de mi blob)
            Nota: Esto va a ser visible solo por el proposito del demo pero al ser info sensible no se deberia mostrar
                 -> 6YCkZrwmH7xNLbHLRAG0IX955UrtQ+OGpgLcVIFfEi9ONCXquzNpo8pVFovijcasZBDxSDPzefZR+ASthNFIYw==

"""

#Credenciales de mi BLOB STORAGE en Azure
storage_account_name = "eontec"
container_name = "despachogeneradora"
access_key = "6YCkZrwmH7xNLbHLRAG0IX955UrtQ+OGpgLcVIFfEi9ONCXquzNpo8pVFovijcasZBDxSDPzefZR+ASthNFIYw=="
blob_name = "DespachoGeneradoraX.xlsx"


#### E.  Conexión y acceso al excel almacenado en Azure blob Storages

En este bloque de código, estoy estableciendo la conexión con Azure Blob Storage usando la librería azure-storage-blob. En lugar de utilizar una firma de acceso compartido (SaaS), he optado por una cadena de conexión, ya que las SAS tienen un tiempo de expiración y para este demo necesitamos un acceso continuo.

Primero, construyo la cadena de conexión usando el nombre de la cuenta y la clave de acceso. Luego, creo un cliente de almacenamiento (BlobServiceClient) que me permite interactuar con el contenedor de blobs. Dentro de este cliente, defino un blob_client que me da acceso directo al archivo de Excel (DespachoGeneradoraX.xlsx) dentro del contenedor despachogeneradora. Finalmente, descargo el archivo completo en memoria para poder procesarlo

In [0]:
"""
    Aqui vamos a conectarnos a nuestro Storage account usando:
    - El cliente de azure (de la libreria azure-storage-blob mediante BlobServiceClient)
    - Usando mi storage_account_name, mi container_name y mi llave de acceso (access_key)

    https://pypi.org/project/azure-storage-blob/ -> Info para utilizar la libreria de azure
    - Nos conectaremos mediante un connection_string, no usaremos una saas ya que esta tiene un tiempo de expiracion
"""

connection_string = f"DefaultEndpointsProtocol=https;AccountName={storage_account_name};AccountKey={access_key};EndpointSuffix=core.windows.net"

#Creo una instancia de azure mediante un cliente
#Libreria de azure me voy a conectar con ud mediante un connection_string con el valor de arriba
#mi cliente se va a llamar blob_service_client
blob_service_client = BlobServiceClient.from_connection_string(
    connection_string
)

#Necesito decirle a mi cliente, cual es el contenedor y el archivo que quiero ver
blob_client = blob_service_client.get_blob_client(
    container=container_name, blob=blob_name
)

#Leyendo el contenido del blob
blob_data = blob_client.download_blob().readall()

METODO 1: Leeyendo el archivo crudo como venga

In [0]:
dfs_pandas_raw = pd.read_excel(blob_data, sheet_name='Hoja1')
display(dfs_pandas_raw)

/databricks/spark/python/pyspark/sql/pandas/conversion.py:401: UserWarning: createDataFrame attempted Arrow optimization because 'spark.sql.execution.arrow.pyspark.enabled' is set to true; however, failed by the reason below:
  Expected bytes, got a 'datetime.datetime' object
Attempting non-optimization as 'spark.sql.execution.arrow.pyspark.fallback.enabled' is set to true.
  warn(msg)


Unnamed: 0 Unnamed: 1 Unnamed: 2 Unnamed: 3 Unnamed: 4 Unnamed: 5 NaN Programa de Generación por Planta NaN NaN NaN NaN NaN Empresa Generadora ACME S.A. E.S.P. NaN NaN NaN NaN NaN Despacho Real 10/07/2024 NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN FECHA PLANTA GENERADOR CAPACIDAD (Kwh) CODIGO NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=0,HOUR_OF_DAY=0,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=1,HOUR_OF_DAY=1,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=2,HOUR_OF_DAY=2,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=3,HOUR_OF_DAY=3,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=4,HOUR_OF_DAY=4,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 20834 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=5,HOUR_OF_DAY=5,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 21626 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=6,HOUR_OF_DAY=6,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 26030 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_

In [0]:
#Transformo mi dataframe de pandas a un dataframe de Spark para utilizar las funcionalidades de spark
dfs_spark_raw = spark.createDataFrame(dfs_pandas_raw) 


---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-1800971018248446>, line 2
      1 #Transformo mi dataframe de pandas a un dataframe de Spark para utilizar las funcionalidades de spark
----> 2 dfs_spark_raw = spark.createDataFrame(dfs_pandas_raw) 

NameError: name 'dfs_pandas_raw' is not defined

METODO 2: LEYENDO EL ARCHIVO SOLO CON LA DATA RELEVANTE (COLUMNAS)

###E.  Lectura del archivo de excel

En este bloque, estoy leyendo el archivo de Excel que descargamos desde Azure Blob Storage y lo estoy convirtiendo en un dataframe utilizando la librería Pandas. Específicamente, estoy cargando la hoja Hoja2 del archivo de Excel en un dataframe llamado dfcapacidad_pandas. Al convertir el archivo en un dataframe, puedo manipular y analizar los datos de una forma mucho más estructurada y eficiente, lo que es ideal para tareas como limpieza de datos, filtrado, o agregación. Finalmente, uso display() para mostrar el contenido del dataframe y asegurarme de que los datos se han cargado correctamente

In [0]:
#Leyendo el archivo de excel desde azure con pandas para que sea un dataframe
dfcapacidad_pandas = pd.read_excel(blob_data, sheet_name='Hoja2')
display(dfcapacidad_pandas)

FECHA PLANTA GENERADOR CAPACIDAD (Kwh) CODIGO 2024-07-10T00:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T01:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T02:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T03:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T04:00:00Z TERMOZIPA 2 20834 ZPA2 2024-07-10T05:00:00Z TERMOZIPA 2 21626 ZPA2 2024-07-10T06:00:00Z TERMOZIPA 2 26030 ZPA2 2024-07-10T07:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T08:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T09:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T10:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T11:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T12:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T13:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T14:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T15:00:00Z TERMOZIPA 2 26294 ZPA2 2024-07-10T16:00:00Z TERMOZIPA 2 28810 ZPA2 2024-07-10T17:00:00Z TERMOZIPA 2 1422 ZPA2 2024-07-10T18:00:00Z TERMOZIPA 2 32084 ZPA2 2024-07-10T19:00:00Z TERMOZIPA 2 30188 ZPA2 2024-07-10T20:00:00Z TERMOZIPA 2 29488 ZPA2 2024-07-10T21:00:00Z TERMOZIPA 2 2944 ZPA2 2024-07-10T22:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T23:00:00Z TERMOZIPA 2 6986 ZPA2 2024-07-10T00:00:00Z TERMOZIPA 3 27042 ZPA3 2024-07-10T01:00:00Z TERMOZIPA 3 27012 ZPA3 2024-07-10T02:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T03:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T04:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T05:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T06:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T07:00:00Z TERMOZIPA 3 28792 ZPA3 2024-07-10T08:00:00Z TERMOZIPA 3 21734 ZPA3 2024-07-10T09:00:00Z TERMOZIPA 3 2092 ZPA3 2024-07-10T10:00:00Z TERMOZIPA 3 2110 ZPA3 2024-07-10T11:00:00Z TERMOZIPA 3 14744 ZPA3 2024-07-10T12:00:00Z TERMOZIPA 3 10106 ZPA3 2024-07-10T13:00:00Z TERMOZIPA 3 24798 ZPA3 2024-07-10T14:00:00Z TERMOZIPA 3 5394 ZPA3 2024-07-10T15:00:00Z TERMOZIPA 3 16960 ZPA3 2024-07-10T16:00:00Z TERMOZIPA 3 6788 ZPA3 2024-07-10T17:00:00Z TERMOZIPA 3 21412 ZPA3 2024-07-10T18:00:00Z TERMOZIPA 3 24676 ZPA3 2024-07-10T19:00:00Z TERMOZIPA 3 21266 ZPA3 2024-07-10T20:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T21:00:00Z TERMOZIPA 3 904 ZPA3 2024-07-10T22:00:00Z TERMOZIPA 3 11280 ZPA3 2024-07-10T23:00:00Z TERMOZIPA 3 2238 ZPA3 2024-07-10T00:00:00Z TERMOZIPA 4 17420 ZPA4 2024-07-10T01:00:00Z TERMOZIPA 4 9402 ZPA4 2024-07-10T02:00:00Z TERMOZIPA 4 29336 ZPA4 2024-07-10T03:00:00Z TERMOZIPA 4 27208 ZPA4 2024-07-10T04:00:00Z TERMOZIPA 4 4940 ZPA4 2024-07-10T05:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T06:00:00Z TERMOZIPA 4 15428 ZPA4 2024-07-10T07:00:00Z TERMOZIPA 4 16152 ZPA4 2024-07-10T08:00:00Z TERMOZIPA 4 30120 ZPA4 2024-07-10T09:00:00Z TERMOZIPA 4 7060 ZPA4 2024-07-10T10:00:00Z TERMOZIPA 4 5360 ZPA4 2024-07-10T11:00:00Z TERMOZIPA 4 27446 ZPA4 2024-07-10T12:00:00Z TERMOZIPA 4 25728 ZPA4 2024-07-10T13:00:00Z TERMOZIPA 4 5008 ZPA4 2024-07-10T14:00:00Z TERMOZIPA 4 27526 ZPA4 2024-07-10T15:00:00Z TERMOZIPA 4 31298 ZPA4 2024-07-10T16:00:00Z TERMOZIPA 4 31824 ZPA4 2024-07-10T17:00:00Z TERMOZIPA 4 2432 ZPA4 2024-07-10T18:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T19:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T20:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T21:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T22:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T23:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T00:00:00Z TERMOZIPA 5 852 ZPA5 2024-07-10T01:00:00Z TERMOZIPA 5 19352 ZPA5 2024-07-10T02:00:00Z TERMOZIPA 5 31480 ZPA5 2024-07-10T03:00:00Z TERMOZIPA 5 3022 ZPA5 2024-07-10T04:00:00Z TERMOZIPA 5 6278 ZPA5 2024-07-10T05:00:00Z TERMOZIPA 5 22228 ZPA5 2024-07-10T06:00:00Z TERMOZIPA 5 24230 ZPA5 2024-07-10T07:00:00Z TERMOZIPA 5 24926 ZPA5 2024-07-10T08:00:00Z TERMOZIPA 5 2304 ZPA5 2024-07-10T09:00:00Z TERMOZIPA 5 23404 ZPA5 2024-07-10T10:00:00Z TERMOZIPA 5 5666 ZPA5 2024-07-10T11:00:00Z TERMOZIPA 5 19354 ZPA5 2024-07-10T12:00:00Z TERMOZIPA 5 8372 ZPA5 2024-07-10T13:00:00Z TERMOZIPA 5 13564 ZPA5 2024-07-10T14:00:00Z TERMOZIPA 5 3806 ZPA5 2024-07-10T15:00:00Z TERMOZIPA 5 32940 ZPA5 2024-07-10T16:00:00Z TERMOZIPA 5 27364 ZPA5 2024-07-10T17:00:00Z TERMOZIPA 5 7164 ZPA5 2024-07-10T18:00:00

###E.  Continuar con la extraccion pero en este caso de la info de la API

En este código, estoy construyendo dos URLs para acceder a una API pública que proporciona datos de precios y despacho de energía. Las URLs se generan dinámicamente utilizando variables de fecha_inicio y fecha_fin, lo que me permite obtener datos para un rango de fechas específico. El datasetId en cada URL identifica el conjunto de datos que quiero consultar: el ID 96D56E se refiere a los precios de energía, mientras que ff027b se refiere al despacho de energía. Estas URLs serán usadas para hacer solicitudes y descargar los datos desde la API.

In [0]:
fecha_inicio = "2024-07-10"
fecha_fin = "2024-07-10"
url_precio_energia = f"https://www.simem.co/backend-files/api/PublicData?startDate={fecha_inicio}&endDate={fecha_fin}&datasetId=96D56E"
url_despacho_energia = f"https://www.simem.co/backend-files/api/PublicData?startdate={fecha_inicio}&enddate={fecha_fin}&datasetId=ff027b"

###E   Obtención datos precios de energía

Este código realiza una petición HTTPS a la API para obtener datos sobre el precio de la energía. Utiliza la librería requests para hacer la solicitud a la URL que ya hemos configurado. Luego, valida si la respuesta fue exitosa revisando el código de estado HTTP (200 indica éxito). Si la solicitud fue exitosa, se extrae la respuesta en formato JSON y se carga en un dataframe de Spark para su procesamiento. En caso de error, se imprime un mensaje para notificar que la solicitud falló.

In [0]:
#PETICION PRECIO ENERGIA

peticion_precio_energia = requests.get(url_precio_energia)
#Debo validar que la respuesta fue exitosa -> codigo: 200
if peticion_precio_energia.status_code == 200:
    print("Respuesta Exitosa, puedo extraer la info sobre precio energia")
    #Extraer la info sobre precio_energia
    dfPrecioEnergia = spark.read.json(sc.parallelize([peticion_precio_energia.text]))
else:
    print("No fue exitosa la peticion para traer la data")


Respuesta Exitosa, puedo extraer la info sobre precio energia


# E

Este comando display(dfPrecioEnergia) se usa para mostrar el contenido del dataframe que hemos cargado a partir de la respuesta de la API. Nos permite visualizar los datos en una tabla, facilitando la verificación de que los datos se han cargado correctamente en Spark y que tienen el formato adecuado para continuar con su análisis o transformación

In [0]:
display(dfPrecioEnergia)

parameters result success List(2024-07-10, 96D56E, 2024-07-10) List(List(List(texto, Código de la variable, CodigoVariable), List(decimal, Valor de la variable, Valor), List(texto, Unidad de medida en la que se encuentra la variable, UnidadMedida), List(texto, Versión de la liquidación, Version), List(texto, Código de duración de la variable en formato ISO8601, CodigoDuracion), List(fecha, Fecha de representación de la información, Fecha)), Fecha, 96D56E, List(Precio de bolsa ponderado, 2023-10-03 15:00:21, Precio de bolsa horario nacional, internacional y TIE, XM, Diaria, NaN, 2024-09-03 09:16:51, Diaria, false), Precio de bolsa ponderado, List(List(P1D, PPBO, 2024-07-10, COP/kWh, 208.5051, TXR), List(P1D, PPBOGReal, 2024-07-10, COP/kWh, 219.7562, TXR), List(P1D, PPBO, 2024-07-10, COP/kWh, 208.5071, TXF), List(P1D, PPBOGReal, 2024-07-10, COP/kWh, 219.7575, TXF), List(P1D, PPBOGReal, 2024-07-10, COP/kWh, 213.6898, TX1), List(P1D, PPBO, 2024-07-10, COP/kWh, 202.4419, TX2), List(P1D, PPBOGReal, 2024-07-10, COP/kWh, 213.6887, TX2)), List(), List(List(Precio de bolsa ponderado con compras en bolsa, COP/kWh, PPBO, Precio de bolsa ponderado con compras en bolsa), List(Precio de bolsa ponderado con la generación real del sistema interconectado nacional, COP/kWh, PPBOGReal, Precio de bolsa ponderado con generación real))) true

In [0]:
#PETICION DESPACHO ENERGIA
peticion_despacho_energia = requests.get(url_despacho_energia)
#Debo validar que la respuesta fue exitosa -> codigo: 200
if peticion_despacho_energia.status_code == 200:
    print("Respuesta Exitosa, puedo extraer la info sobre despacho energia")
    #Extraer la info sobre precio_energia
    dfDespachoEnergia = spark.read.json(sc.parallelize([peticion_despacho_energia.text]))
    print(peticion_despacho_energia.text)

else:
    print("No fue exitosa la peticion para traer la data")

Respuesta Exitosa, puedo extraer la info sobre despacho energia
{"parameters":{"idDataset":"ff027b","startDate":"2024-07-10","endDate":"2024-07-10"},"success":true,"result":{"idDataset":"ff027b","name":"Despacho programado recursos de generación","metadata":{"description":"Contiene el programa de generación del despacho económico en kW","creationDate":"2023-09-30 10:52:26","lastUpdate":"2024-09-07 00:04:58","entity":"XM","category":"Despacho programado recursos de generación","periodicity":"Diaria","granularity":"Horaria","historicData":"https://www.xm.com.co/corto-plazo/despacho-energia/informe-del-despacho","private":false},"filterDate":"FechaHora","records":[{"FechaHora":"2024-07-10 00:00:00","CodigoDuracion":"PT1H","CodigoPlanta":"2QBW","Valor":14000.0000},{"FechaHora":"2024-07-10 00:00:00","CodigoDuracion":"PT1H","CodigoPlanta":"2QEK","Valor":35000.0000},{"FechaHora":"2024-07-10 00:00:00","CodigoDuracion":"PT1H","CodigoPlanta":"2QRL","Valor":630.0000},{"FechaHora":"2024-07-10 00:0

In [0]:
display(dfDespachoEnergia)

parameters result success List(2024-07-10, ff027b, 2024-07-10) List(List(List(decimal, Valor de la variable, Valor), List(texto, Código de la planta, CodigoPlanta), List(fecha hora, Fecha y hora de representación del dato, FechaHora), List(texto, Código de duración de la variable en formato ISO8601, CodigoDuracion)), FechaHora, ff027b, List(Despacho programado recursos de generación, 2023-09-30 10:52:26, Contiene el programa de generación del despacho económico en kW, XM, Horaria, https://www.xm.com.co/corto-plazo/despacho-energia/informe-del-despacho, 2024-09-07 00:04:58, Diaria, false), Despacho programado recursos de generación, List(List(PT1H, 2QBW, 2024-07-10 00:00:00, 14000.0), List(PT1H, 2QEK, 2024-07-10 00:00:00, 35000.0), List(PT1H, 2QRL, 2024-07-10 00:00:00, 630.0), List(PT1H, 2QV2, 2024-07-10 00:00:00, 18000.0), List(PT1H, 2R22, 2024-07-10 00:00:00, 14000.0), List(PT1H, 2S6Q, 2024-07-10 00:00:00, 0.0), List(PT1H, 2S6S, 2024-07-10 00:00:00, 0.0), List(PT1H, 2S6U, 2024-07-10 00:00:00, 6500.0), List(PT1H, 2S78, 2024-07-10 00:00:00, 340.0), List(PT1H, 2S8I, 2024-07-10 00:00:00, 8000.0), List(PT1H, 2S8N, 2024-07-10 00:00:00, 0.0), List(PT1H, 2S8S, 2024-07-10 00:00:00, 250.0), List(PT1H, 2S8U, 2024-07-10 00:00:00, 1500.0), List(PT1H, 2S9L, 2024-07-10 00:00:00, 450.0), List(PT1H, 2S9Q, 2024-07-10 00:00:00, 0.0), List(PT1H, 2SDR, 2024-07-10 00:00:00, 6900.0), List(PT1H, 2SI1, 2024-07-10 00:00:00, 18000.0), List(PT1H, 2SS2, 2024-07-10 00:00:00, 5200.0), List(PT1H, 2SW1, 2024-07-10 00:00:00, 16500.0), List(PT1H, 2SXQ, 2024-07-10 00:00:00, 0.0), List(PT1H, 2T1L, 2024-07-10 00:00:00, 18000.0), List(PT1H, 2T4P, 2024-07-10 00:00:00, 18000.0), List(PT1H, 2T7D, 2024-07-10 00:00:00, 2820.0), List(PT1H, 2TUT, 2024-07-10 00:00:00, 19600.0), List(PT1H, 2TUV, 2024-07-10 00:00:00, 19600.0), List(PT1H, 2TYI, 2024-07-10 00:00:00, 0.0), List(PT1H, 2U1G, 2024-07-10 00:00:00, 1400.0), List(PT1H, 2U5P, 2024-07-10 00:00:00, 0.0), List(PT1H, 2U8Y, 2024-07-10 00:00:00, 19300.0), List(PT1H, 2U91, 2024-07-10 00:00:00, 19300.0), List(PT1H, 2U93, 2024-07-10 00:00:00, 19300.0), List(PT1H, 2UP2, 2024-07-10 00:00:00, 9000.0), List(PT1H, 2UPD, 2024-07-10 00:00:00, 11000.0), List(PT1H, 2UPF, 2024-07-10 00:00:00, 12000.0), List(PT1H, 2UPH, 2024-07-10 00:00:00, 11000.0), List(PT1H, 2UPJ, 2024-07-10 00:00:00, 12000.0), List(PT1H, 2UR5, 2024-07-10 00:00:00, 900.0), List(PT1H, 2UX3, 2024-07-10 00:00:00, 17600.0), List(PT1H, 2V25, 2024-07-10 00:00:00, 900.0), List(PT1H, 2V27, 2024-07-10 00:00:00, 400.0), List(PT1H, 2V5G, 2024-07-10 00:00:00, 3800.0), List(PT1H, 2VJS, 2024-07-10 00:00:00, 0.0), List(PT1H, 2WC5, 2024-07-10 00:00:00, 7320.0), List(PT1H, 2WFN, 2024-07-10 00:00:00, 3000.0), List(PT1H, 2XXR, 2024-07-10 00:00:00, 0.0), List(PT1H, 2YB9, 2024-07-10 00:00:00, 1000.0), List(PT1H, 2YIR, 2024-07-10 00:00:00, 210.0), List(PT1H, 2YNA, 2024-07-10 00:00:00, 3100.0), List(PT1H, 2YWY, 2024-07-10 00:00:00, 3500.0), List(PT1H, 2ZCF, 2024-07-10 00:00:00, 10000.0), List(PT1H, 2ZHY, 2024-07-10 00:00:00, 0.0), List(PT1H, 2ZP9, 2024-07-10 00:00:00, 0.0), List(PT1H, 3A44, 2024-07-10 00:00:00, 0.0), List(PT1H, 3ACC, 2024-07-10 00:00:00, 0.0), List(PT1H, 3ADA, 2024-07-10 00:00:00, 380.0), List(PT1H, 3AFQ, 2024-07-10 00:00:00, 1000.0), List(PT1H, 3AQP, 2024-07-10 00:00:00, 200.0), List(PT1H, 3B4L, 2024-07-10 00:00:00, 0.0), List(PT1H, 3BZB, 2024-07-10 00:00:00, 0.0), List(PT1H, 3C3X, 2024-07-10 00:00:00, 200.0), List(PT1H, 3C3Z, 2024-07-10 00:00:00, 0.0), List(PT1H, 3C4V, 2024-07-10 00:00:00, 2800.0), List(PT1H, 3CG9, 2024-07-10 00:00:00, 4000.0), List(PT1H, 3CSH, 2024-07-10 00:00:00, 0.0), List(PT1H, 3DDT, 2024-07-10 00:00:00, 0.0), List(PT1H, 3DSO, 2024-07-10 00:00:00, 0.0), List(PT1H, 3DXJ, 2024-07-10 00:00:00, 450.0), List(PT1H, 3E7C, 2024-07-10 00:00:00, 0.0), List(PT1H, 3E9I, 2024-07-10 00:00:00, 8700.0), List(PT1H, 3EBN, 2024-07-10 00:00:00, 0.0), List(PT1H, 3ED1, 2024-07-10 00:00:00, 0.0), List(PT1H, 3EDL, 2024-07-10 00:00:00, 0.0), List(PT1H, 3EE4, 2024-07-10 00:00

#TRANSFORMACIÓN

En este paso, estamos transformando el dataframe dfcapacidad_pandas, que inicialmente era un dataframe de Pandas, en un dataframe de Spark (dfCapacidad_spark). Esto nos permite aprovechar las funcionalidades distribuidas y escalables de Spark para procesar grandes volúmenes de datos. Utilizamos la sesión de Spark que habíamos definido anteriormente y, al final, mostramos el dataframe para verificar su contenido y formato

In [0]:
#Transformo mi dataframe df_capacidad de pandas a uno de spark para usar las funcionalidades de spark
#para esto hago uso de la sesion de spark que defini al inicio de mi codigo, para trabajar con spark 

dfCapacidad_spark = spark.createDataFrame(dfcapacidad_pandas)
display(dfCapacidad_spark)

FECHA PLANTA GENERADOR CAPACIDAD (Kwh) CODIGO 2024-07-10T00:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T01:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T02:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T03:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T04:00:00Z TERMOZIPA 2 20834 ZPA2 2024-07-10T05:00:00Z TERMOZIPA 2 21626 ZPA2 2024-07-10T06:00:00Z TERMOZIPA 2 26030 ZPA2 2024-07-10T07:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T08:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T09:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T10:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T11:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T12:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T13:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T14:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T15:00:00Z TERMOZIPA 2 26294 ZPA2 2024-07-10T16:00:00Z TERMOZIPA 2 28810 ZPA2 2024-07-10T17:00:00Z TERMOZIPA 2 1422 ZPA2 2024-07-10T18:00:00Z TERMOZIPA 2 32084 ZPA2 2024-07-10T19:00:00Z TERMOZIPA 2 30188 ZPA2 2024-07-10T20:00:00Z TERMOZIPA 2 29488 ZPA2 2024-07-10T21:00:00Z TERMOZIPA 2 2944 ZPA2 2024-07-10T22:00:00Z TERMOZIPA 2 33000 ZPA2 2024-07-10T23:00:00Z TERMOZIPA 2 6986 ZPA2 2024-07-10T00:00:00Z TERMOZIPA 3 27042 ZPA3 2024-07-10T01:00:00Z TERMOZIPA 3 27012 ZPA3 2024-07-10T02:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T03:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T04:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T05:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T06:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T07:00:00Z TERMOZIPA 3 28792 ZPA3 2024-07-10T08:00:00Z TERMOZIPA 3 21734 ZPA3 2024-07-10T09:00:00Z TERMOZIPA 3 2092 ZPA3 2024-07-10T10:00:00Z TERMOZIPA 3 2110 ZPA3 2024-07-10T11:00:00Z TERMOZIPA 3 14744 ZPA3 2024-07-10T12:00:00Z TERMOZIPA 3 10106 ZPA3 2024-07-10T13:00:00Z TERMOZIPA 3 24798 ZPA3 2024-07-10T14:00:00Z TERMOZIPA 3 5394 ZPA3 2024-07-10T15:00:00Z TERMOZIPA 3 16960 ZPA3 2024-07-10T16:00:00Z TERMOZIPA 3 6788 ZPA3 2024-07-10T17:00:00Z TERMOZIPA 3 21412 ZPA3 2024-07-10T18:00:00Z TERMOZIPA 3 24676 ZPA3 2024-07-10T19:00:00Z TERMOZIPA 3 21266 ZPA3 2024-07-10T20:00:00Z TERMOZIPA 3 33000 ZPA3 2024-07-10T21:00:00Z TERMOZIPA 3 904 ZPA3 2024-07-10T22:00:00Z TERMOZIPA 3 11280 ZPA3 2024-07-10T23:00:00Z TERMOZIPA 3 2238 ZPA3 2024-07-10T00:00:00Z TERMOZIPA 4 17420 ZPA4 2024-07-10T01:00:00Z TERMOZIPA 4 9402 ZPA4 2024-07-10T02:00:00Z TERMOZIPA 4 29336 ZPA4 2024-07-10T03:00:00Z TERMOZIPA 4 27208 ZPA4 2024-07-10T04:00:00Z TERMOZIPA 4 4940 ZPA4 2024-07-10T05:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T06:00:00Z TERMOZIPA 4 15428 ZPA4 2024-07-10T07:00:00Z TERMOZIPA 4 16152 ZPA4 2024-07-10T08:00:00Z TERMOZIPA 4 30120 ZPA4 2024-07-10T09:00:00Z TERMOZIPA 4 7060 ZPA4 2024-07-10T10:00:00Z TERMOZIPA 4 5360 ZPA4 2024-07-10T11:00:00Z TERMOZIPA 4 27446 ZPA4 2024-07-10T12:00:00Z TERMOZIPA 4 25728 ZPA4 2024-07-10T13:00:00Z TERMOZIPA 4 5008 ZPA4 2024-07-10T14:00:00Z TERMOZIPA 4 27526 ZPA4 2024-07-10T15:00:00Z TERMOZIPA 4 31298 ZPA4 2024-07-10T16:00:00Z TERMOZIPA 4 31824 ZPA4 2024-07-10T17:00:00Z TERMOZIPA 4 2432 ZPA4 2024-07-10T18:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T19:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T20:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T21:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T22:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T23:00:00Z TERMOZIPA 4 33000 ZPA4 2024-07-10T00:00:00Z TERMOZIPA 5 852 ZPA5 2024-07-10T01:00:00Z TERMOZIPA 5 19352 ZPA5 2024-07-10T02:00:00Z TERMOZIPA 5 31480 ZPA5 2024-07-10T03:00:00Z TERMOZIPA 5 3022 ZPA5 2024-07-10T04:00:00Z TERMOZIPA 5 6278 ZPA5 2024-07-10T05:00:00Z TERMOZIPA 5 22228 ZPA5 2024-07-10T06:00:00Z TERMOZIPA 5 24230 ZPA5 2024-07-10T07:00:00Z TERMOZIPA 5 24926 ZPA5 2024-07-10T08:00:00Z TERMOZIPA 5 2304 ZPA5 2024-07-10T09:00:00Z TERMOZIPA 5 23404 ZPA5 2024-07-10T10:00:00Z TERMOZIPA 5 5666 ZPA5 2024-07-10T11:00:00Z TERMOZIPA 5 19354 ZPA5 2024-07-10T12:00:00Z TERMOZIPA 5 8372 ZPA5 2024-07-10T13:00:00Z TERMOZIPA 5 13564 ZPA5 2024-07-10T14:00:00Z TERMOZIPA 5 3806 ZPA5 2024-07-10T15:00:00Z TERMOZIPA 5 32940 ZPA5 2024-07-10T16:00:00Z TERMOZIPA 5 27364 ZPA5 2024-07-10T17:00:00Z TERMOZIPA 5 7164 ZPA5 2024-07-10T18:00:00

##### T.  Transformación Fechas

En este paso, estamos utilizando Spark para transformar el formato de la columna FECHA en nuestro dataframe. Para ello, usamos la función withColumn, que nos permite modificar una columna específica. También empleamos to_date, una función de Spark que transforma el valor de la columna FECHA a un formato de fecha estándar (en este caso, "YYYY-MM-DD"). Esto es crucial para asegurar que las fechas se procesen de manera correcta y sean utilizables en análisis futuros

In [0]:
"""
    Voy a transformar el formato de la FECHA para que quede en formato "YYYY-MM-DD"
    spark tiene una funcion llamada withColumn que me permite llamar o hacer alguna accion sobre una columna de mi dataframe simplemente llamandola por el nombre de esta, asi que en este caso le dire que haga algo sobre la columna fecha

    Ademas, spark cuenta con una funcion que se llama to_date que me permite transformar un dato hacia una fecha en el formato que yo le especifique
"""

dfCapacidad_spark = dfCapacidad_spark.withColumn("FECHA",to_date(col("FECHA"),"YYYY-MM-DD"))

T.  El comando display(df_capacidad_spark) se utiliza para mostrar el dataframe df_capacidad_spark en formato tabular. Esto es útil para validar y explorar los datos después de cargarlos y transformarlos en Spark, asegurando que la información esté correcta y en el formato adecuado para análisis posteriores

In [0]:
display(dfCapacidad_spark)

FECHA PLANTA GENERADOR CAPACIDAD (Kwh) CODIGO 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 20834 ZPA2 2024-07-10 TERMOZIPA 2 21626 ZPA2 2024-07-10 TERMOZIPA 2 26030 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 26294 ZPA2 2024-07-10 TERMOZIPA 2 28810 ZPA2 2024-07-10 TERMOZIPA 2 1422 ZPA2 2024-07-10 TERMOZIPA 2 32084 ZPA2 2024-07-10 TERMOZIPA 2 30188 ZPA2 2024-07-10 TERMOZIPA 2 29488 ZPA2 2024-07-10 TERMOZIPA 2 2944 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 6986 ZPA2 2024-07-10 TERMOZIPA 3 27042 ZPA3 2024-07-10 TERMOZIPA 3 27012 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 28792 ZPA3 2024-07-10 TERMOZIPA 3 21734 ZPA3 2024-07-10 TERMOZIPA 3 2092 ZPA3 2024-07-10 TERMOZIPA 3 2110 ZPA3 2024-07-10 TERMOZIPA 3 14744 ZPA3 2024-07-10 TERMOZIPA 3 10106 ZPA3 2024-07-10 TERMOZIPA 3 24798 ZPA3 2024-07-10 TERMOZIPA 3 5394 ZPA3 2024-07-10 TERMOZIPA 3 16960 ZPA3 2024-07-10 TERMOZIPA 3 6788 ZPA3 2024-07-10 TERMOZIPA 3 21412 ZPA3 2024-07-10 TERMOZIPA 3 24676 ZPA3 2024-07-10 TERMOZIPA 3 21266 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 904 ZPA3 2024-07-10 TERMOZIPA 3 11280 ZPA3 2024-07-10 TERMOZIPA 3 2238 ZPA3 2024-07-10 TERMOZIPA 4 17420 ZPA4 2024-07-10 TERMOZIPA 4 9402 ZPA4 2024-07-10 TERMOZIPA 4 29336 ZPA4 2024-07-10 TERMOZIPA 4 27208 ZPA4 2024-07-10 TERMOZIPA 4 4940 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 15428 ZPA4 2024-07-10 TERMOZIPA 4 16152 ZPA4 2024-07-10 TERMOZIPA 4 30120 ZPA4 2024-07-10 TERMOZIPA 4 7060 ZPA4 2024-07-10 TERMOZIPA 4 5360 ZPA4 2024-07-10 TERMOZIPA 4 27446 ZPA4 2024-07-10 TERMOZIPA 4 25728 ZPA4 2024-07-10 TERMOZIPA 4 5008 ZPA4 2024-07-10 TERMOZIPA 4 27526 ZPA4 2024-07-10 TERMOZIPA 4 31298 ZPA4 2024-07-10 TERMOZIPA 4 31824 ZPA4 2024-07-10 TERMOZIPA 4 2432 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 5 852 ZPA5 2024-07-10 TERMOZIPA 5 19352 ZPA5 2024-07-10 TERMOZIPA 5 31480 ZPA5 2024-07-10 TERMOZIPA 5 3022 ZPA5 2024-07-10 TERMOZIPA 5 6278 ZPA5 2024-07-10 TERMOZIPA 5 22228 ZPA5 2024-07-10 TERMOZIPA 5 24230 ZPA5 2024-07-10 TERMOZIPA 5 24926 ZPA5 2024-07-10 TERMOZIPA 5 2304 ZPA5 2024-07-10 TERMOZIPA 5 23404 ZPA5 2024-07-10 TERMOZIPA 5 5666 ZPA5 2024-07-10 TERMOZIPA 5 19354 ZPA5 2024-07-10 TERMOZIPA 5 8372 ZPA5 2024-07-10 TERMOZIPA 5 13564 ZPA5 2024-07-10 TERMOZIPA 5 3806 ZPA5 2024-07-10 TERMOZIPA 5 32940 ZPA5 2024-07-10 TERMOZIPA 5 27364 ZPA5 2024-07-10 TERMOZIPA 5 7164 ZPA5 2024-07-10 TERMOZIPA 5 22170 ZPA5 2024-07-10 TERMOZIPA 5 15448 ZPA5 2024-07-10 TERMOZIPA 5 24080 ZPA5 2024-07-10 TERMOZIPA 5 17704 ZPA5 2024-07-10 TERMOZIPA 5 16420 ZPA5 2024-07-10 TERMOZIPA 5 13812 ZPA5 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1161384 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 441756 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 353958 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 907200 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1150828 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 199938 GVIO 2024-07-10 GUAVIO 1 645326 GVIO 2024-07-10 GUAVIO 1 1200000

In [0]:
dfCapacidad_spark.createOrReplaceTempView("Capacidad")

##T.  

En este punto vamos a revisar la data de dfCapacidad para identificar especificamente el conjunto de plantas que seran de nuestro interes
esto nos permitira restringir el analisis con respecto a la data de XM solo para los codigos de las plantas que coincidan con las que se tiene en dfCapacidad

Para esto solo utilizare SQL para validar las plantas existentes sin duplicados

In [0]:
%sql
SELECT DISTINCT(CODIGO)
FROM Capacidad

CODIGO ZPA2 ZPA3 ZPA4 ZPA5 GVIO QUI1

### (*T*) Filtrado de los atributos que traen el precio de bolsa


La documentación del API nos muestra que trae muchas columnas de información, denominados metadatos, necesitamos puntualmente los datos válidos para nuestro análisis. 

```
CodigoDuracion:string
CodigoPlanta:string
FechaHora:string
Valor:long
```

En estas 3 celdas, transformamos el formato utilizando funciones como aplanar o explotar, colocando alias y realizando un filtro o un select.


In [0]:
dfPrecioEnergialimpio=dfPrecioEnergia.select(explode(col("result.records")).alias("results")).select(col("results.*"))

In [0]:
display(dfPrecioEnergialimpio)

CodigoDuracion CodigoVariable Fecha UnidadMedida Valor Version P1D PPBO 2024-07-10 COP/kWh 208.5051 TXR P1D PPBOGReal 2024-07-10 COP/kWh 219.7562 TXR P1D PPBO 2024-07-10 COP/kWh 208.5071 TXF P1D PPBOGReal 2024-07-10 COP/kWh 219.7575 TXF P1D PPBOGReal 2024-07-10 COP/kWh 213.6898 TX1 P1D PPBO 2024-07-10 COP/kWh 202.4419 TX2 P1D PPBOGReal 2024-07-10 COP/kWh 213.6887 TX2

In [0]:
dfPrecioEnergialimpio.createOrReplaceTempView("Precios")

### (*T*) Filtrado de los atributos que traen el despacho de las plantas

Al igual que los precios de bolsa, el API de los despachos trae datos excesivos, que no necesitamos, vamos a extraer los datos de utilidad:


```
CodigoDuracion:string
CodigoPlanta:string
FechaHora:string
Valor:long
```
Al igual que en el caso anterior, en las próximas 3 celdas aplanamos estructuras, renombramos con un alias y filtramos con una selección.

In [0]:
dfResultsdfDespachoEnergia=dfDespachoEnergia.select(explode(col("result.records")).alias("results")).select(col("results.*"))

In [0]:
display(dfResultsdfDespachoEnergia)

CodigoDuracion CodigoPlanta FechaHora Valor PT1H 2QBW 2024-07-10 00:00:00 14000.0 PT1H 2QEK 2024-07-10 00:00:00 35000.0 PT1H 2QRL 2024-07-10 00:00:00 630.0 PT1H 2QV2 2024-07-10 00:00:00 18000.0 PT1H 2R22 2024-07-10 00:00:00 14000.0 PT1H 2S6Q 2024-07-10 00:00:00 0.0 PT1H 2S6S 2024-07-10 00:00:00 0.0 PT1H 2S6U 2024-07-10 00:00:00 6500.0 PT1H 2S78 2024-07-10 00:00:00 340.0 PT1H 2S8I 2024-07-10 00:00:00 8000.0 PT1H 2S8N 2024-07-10 00:00:00 0.0 PT1H 2S8S 2024-07-10 00:00:00 250.0 PT1H 2S8U 2024-07-10 00:00:00 1500.0 PT1H 2S9L 2024-07-10 00:00:00 450.0 PT1H 2S9Q 2024-07-10 00:00:00 0.0 PT1H 2SDR 2024-07-10 00:00:00 6900.0 PT1H 2SI1 2024-07-10 00:00:00 18000.0 PT1H 2SS2 2024-07-10 00:00:00 5200.0 PT1H 2SW1 2024-07-10 00:00:00 16500.0 PT1H 2SXQ 2024-07-10 00:00:00 0.0 PT1H 2T1L 2024-07-10 00:00:00 18000.0 PT1H 2T4P 2024-07-10 00:00:00 18000.0 PT1H 2T7D 2024-07-10 00:00:00 2820.0 PT1H 2TUT 2024-07-10 00:00:00 19600.0 PT1H 2TUV 2024-07-10 00:00:00 19600.0 PT1H 2TYI 2024-07-10 00:00:00 0.0 PT1H 2U1G 2024-07-10 00:00:00 1400.0 PT1H 2U5P 2024-07-10 00:00:00 0.0 PT1H 2U8Y 2024-07-10 00:00:00 19300.0 PT1H 2U91 2024-07-10 00:00:00 19300.0 PT1H 2U93 2024-07-10 00:00:00 19300.0 PT1H 2UP2 2024-07-10 00:00:00 9000.0 PT1H 2UPD 2024-07-10 00:00:00 11000.0 PT1H 2UPF 2024-07-10 00:00:00 12000.0 PT1H 2UPH 2024-07-10 00:00:00 11000.0 PT1H 2UPJ 2024-07-10 00:00:00 12000.0 PT1H 2UR5 2024-07-10 00:00:00 900.0 PT1H 2UX3 2024-07-10 00:00:00 17600.0 PT1H 2V25 2024-07-10 00:00:00 900.0 PT1H 2V27 2024-07-10 00:00:00 400.0 PT1H 2V5G 2024-07-10 00:00:00 3800.0 PT1H 2VJS 2024-07-10 00:00:00 0.0 PT1H 2WC5 2024-07-10 00:00:00 7320.0 PT1H 2WFN 2024-07-10 00:00:00 3000.0 PT1H 2XXR 2024-07-10 00:00:00 0.0 PT1H 2YB9 2024-07-10 00:00:00 1000.0 PT1H 2YIR 2024-07-10 00:00:00 210.0 PT1H 2YNA 2024-07-10 00:00:00 3100.0 PT1H 2YWY 2024-07-10 00:00:00 3500.0 PT1H 2ZCF 2024-07-10 00:00:00 10000.0 PT1H 2ZHY 2024-07-10 00:00:00 0.0 PT1H 2ZP9 2024-07-10 00:00:00 0.0 PT1H 3A44 2024-07-10 00:00:00 0.0 PT1H 3ACC 2024-07-10 00:00:00 0.0 PT1H 3ADA 2024-07-10 00:00:00 380.0 PT1H 3AFQ 2024-07-10 00:00:00 1000.0 PT1H 3AQP 2024-07-10 00:00:00 200.0 PT1H 3B4L 2024-07-10 00:00:00 0.0 PT1H 3BZB 2024-07-10 00:00:00 0.0 PT1H 3C3X 2024-07-10 00:00:00 200.0 PT1H 3C3Z 2024-07-10 00:00:00 0.0 PT1H 3C4V 2024-07-10 00:00:00 2800.0 PT1H 3CG9 2024-07-10 00:00:00 4000.0 PT1H 3CSH 2024-07-10 00:00:00 0.0 PT1H 3DDT 2024-07-10 00:00:00 0.0 PT1H 3DSO 2024-07-10 00:00:00 0.0 PT1H 3DXJ 2024-07-10 00:00:00 450.0 PT1H 3E7C 2024-07-10 00:00:00 0.0 PT1H 3E9I 2024-07-10 00:00:00 8700.0 PT1H 3EBN 2024-07-10 00:00:00 0.0 PT1H 3ED1 2024-07-10 00:00:00 0.0 PT1H 3EDL 2024-07-10 00:00:00 0.0 PT1H 3EE4 2024-07-10 00:00:00 18000.0 PT1H 3EFY 2024-07-10 00:00:00 0.0 PT1H 3ENA 2024-07-10 00:00:00 0.0 PT1H 3ENE 2024-07-10 00:00:00 0.0 PT1H 3EP6 2024-07-10 00:00:00 0.0 PT1H 3EV1 2024-07-10 00:00:00 0.0 PT1H 3EV3 2024-07-10 00:00:00 0.0 PT1H 3EXB 2024-07-10 00:00:00 0.0 PT1H 3EXH 2024-07-10 00:00:00 11780.0 PT1H 3F5L 2024-07-10 00:00:00 0.0 PT1H 3F5N 2024-07-10 00:00:00 0.0 PT1H 3FCD 2024-07-10 00:00:00 0.0 PT1H 3FCF 2024-07-10 00:00:00 0.0 PT1H 3GI6 2024-07-10 00:00:00 0.0 PT1H 3GJQ 2024-07-10 00:00:00 0.0 PT1H 3GJU 2024-07-10 00:00:00 500.0 PT1H 3GPZ 2024-07-10 00:00:00 0.0 PT1H 3GRD 2024-07-10 00:00:00 0.0 PT1H 3GSF 2024-07-10 00:00:00 0.0 PT1H 3GVI 2024-07-10 00:00:00 0.0 PT1H 3GVK 2024-07-10 00:00:00 0.0 PT1H 3GVM 2024-07-10 00:00:00 0.0 PT1H 3H2U 2024-07-10 00:00:00 9800.0 PT1H 3HBN 2024-07-10 00:00:00 0.0 PT1H 3HBP 2024-07-10 00:00:00 0.0 PT1H 3HDE 2024-07-10 00:00:00 19900.0 PT1H 3HDG 2024-07-10 00:00:00 19900.0 PT1H 3HE8 2024-07-10 00:00:00 0.0 PT1H 3HF5 2024-07-10 00:00:00 0.0 PT1H 3HF7 2024-07-10 00:00:00 0.0 PT1H 3HF9 2024-07-10 00:00:00 0.0 PT1H 3HG7 2024-07-10 00:00:00 0.0 PT1H 3HG9 2024-07-10 00:00:00 0.0 PT1H 3HLD 2024-07-10 00:00:00 0.0 PT1H 3HS9 2024-07-10 00:00:00 0.0 PT1H 3HWM 2024-07-10 00:00:00 0.0 PT1H 3HYG 2024-07-10 00:00:00 0.0 PT1H 3IJF 2024-07-10 00:00:00 1000.0 PT1H 3INX 2024-07-10 00:00:00 0.0 PT1H

In [0]:
dfResultsdfDespachoEnergia = dfResultsdfDespachoEnergia.withColumn("FechaHora", substring("FechaHora",1,10)).withColumnRenamed("FechaHora", "Fecha").withColumnRenamed("Valor", "Compromiso")

In [0]:
display(dfResultsdfDespachoEnergia)

CodigoDuracion CodigoPlanta Fecha Compromiso PT1H 2QBW 2024-07-10 14000.0 PT1H 2QEK 2024-07-10 35000.0 PT1H 2QRL 2024-07-10 630.0 PT1H 2QV2 2024-07-10 18000.0 PT1H 2R22 2024-07-10 14000.0 PT1H 2S6Q 2024-07-10 0.0 PT1H 2S6S 2024-07-10 0.0 PT1H 2S6U 2024-07-10 6500.0 PT1H 2S78 2024-07-10 340.0 PT1H 2S8I 2024-07-10 8000.0 PT1H 2S8N 2024-07-10 0.0 PT1H 2S8S 2024-07-10 250.0 PT1H 2S8U 2024-07-10 1500.0 PT1H 2S9L 2024-07-10 450.0 PT1H 2S9Q 2024-07-10 0.0 PT1H 2SDR 2024-07-10 6900.0 PT1H 2SI1 2024-07-10 18000.0 PT1H 2SS2 2024-07-10 5200.0 PT1H 2SW1 2024-07-10 16500.0 PT1H 2SXQ 2024-07-10 0.0 PT1H 2T1L 2024-07-10 18000.0 PT1H 2T4P 2024-07-10 18000.0 PT1H 2T7D 2024-07-10 2820.0 PT1H 2TUT 2024-07-10 19600.0 PT1H 2TUV 2024-07-10 19600.0 PT1H 2TYI 2024-07-10 0.0 PT1H 2U1G 2024-07-10 1400.0 PT1H 2U5P 2024-07-10 0.0 PT1H 2U8Y 2024-07-10 19300.0 PT1H 2U91 2024-07-10 19300.0 PT1H 2U93 2024-07-10 19300.0 PT1H 2UP2 2024-07-10 9000.0 PT1H 2UPD 2024-07-10 11000.0 PT1H 2UPF 2024-07-10 12000.0 PT1H 2UPH 2024-07-10 11000.0 PT1H 2UPJ 2024-07-10 12000.0 PT1H 2UR5 2024-07-10 900.0 PT1H 2UX3 2024-07-10 17600.0 PT1H 2V25 2024-07-10 900.0 PT1H 2V27 2024-07-10 400.0 PT1H 2V5G 2024-07-10 3800.0 PT1H 2VJS 2024-07-10 0.0 PT1H 2WC5 2024-07-10 7320.0 PT1H 2WFN 2024-07-10 3000.0 PT1H 2XXR 2024-07-10 0.0 PT1H 2YB9 2024-07-10 1000.0 PT1H 2YIR 2024-07-10 210.0 PT1H 2YNA 2024-07-10 3100.0 PT1H 2YWY 2024-07-10 3500.0 PT1H 2ZCF 2024-07-10 10000.0 PT1H 2ZHY 2024-07-10 0.0 PT1H 2ZP9 2024-07-10 0.0 PT1H 3A44 2024-07-10 0.0 PT1H 3ACC 2024-07-10 0.0 PT1H 3ADA 2024-07-10 380.0 PT1H 3AFQ 2024-07-10 1000.0 PT1H 3AQP 2024-07-10 200.0 PT1H 3B4L 2024-07-10 0.0 PT1H 3BZB 2024-07-10 0.0 PT1H 3C3X 2024-07-10 200.0 PT1H 3C3Z 2024-07-10 0.0 PT1H 3C4V 2024-07-10 2800.0 PT1H 3CG9 2024-07-10 4000.0 PT1H 3CSH 2024-07-10 0.0 PT1H 3DDT 2024-07-10 0.0 PT1H 3DSO 2024-07-10 0.0 PT1H 3DXJ 2024-07-10 450.0 PT1H 3E7C 2024-07-10 0.0 PT1H 3E9I 2024-07-10 8700.0 PT1H 3EBN 2024-07-10 0.0 PT1H 3ED1 2024-07-10 0.0 PT1H 3EDL 2024-07-10 0.0 PT1H 3EE4 2024-07-10 18000.0 PT1H 3EFY 2024-07-10 0.0 PT1H 3ENA 2024-07-10 0.0 PT1H 3ENE 2024-07-10 0.0 PT1H 3EP6 2024-07-10 0.0 PT1H 3EV1 2024-07-10 0.0 PT1H 3EV3 2024-07-10 0.0 PT1H 3EXB 2024-07-10 0.0 PT1H 3EXH 2024-07-10 11780.0 PT1H 3F5L 2024-07-10 0.0 PT1H 3F5N 2024-07-10 0.0 PT1H 3FCD 2024-07-10 0.0 PT1H 3FCF 2024-07-10 0.0 PT1H 3GI6 2024-07-10 0.0 PT1H 3GJQ 2024-07-10 0.0 PT1H 3GJU 2024-07-10 500.0 PT1H 3GPZ 2024-07-10 0.0 PT1H 3GRD 2024-07-10 0.0 PT1H 3GSF 2024-07-10 0.0 PT1H 3GVI 2024-07-10 0.0 PT1H 3GVK 2024-07-10 0.0 PT1H 3GVM 2024-07-10 0.0 PT1H 3H2U 2024-07-10 9800.0 PT1H 3HBN 2024-07-10 0.0 PT1H 3HBP 2024-07-10 0.0 PT1H 3HDE 2024-07-10 19900.0 PT1H 3HDG 2024-07-10 19900.0 PT1H 3HE8 2024-07-10 0.0 PT1H 3HF5 2024-07-10 0.0 PT1H 3HF7 2024-07-10 0.0 PT1H 3HF9 2024-07-10 0.0 PT1H 3HG7 2024-07-10 0.0 PT1H 3HG9 2024-07-10 0.0 PT1H 3HLD 2024-07-10 0.0 PT1H 3HS9 2024-07-10 0.0 PT1H 3HWM 2024-07-10 0.0 PT1H 3HYG 2024-07-10 0.0 PT1H 3IJF 2024-07-10 1000.0 PT1H 3INX 2024-07-10 0.0 PT1H 3IQA 2024-07-10 0.0 PT1H 3IRX 2024-07-10 0.0 PT1H 3IRZ 2024-07-10 700.0 PT1H 3IS2 2024-07-10 0.0 PT1H 3IZ6 2024-07-10 0.0 PT1H 3J1J 2024-07-10 0.0 PT1H 3J2B 2024-07-10 0.0 PT1H 3J2H 2024-07-10 0.0 PT1H 3J4D 2024-07-10 0.0 PT1H 3J4R 2024-07-10 0.0 PT1H 3J4T 2024-07-10 0.0 PT1H 3J4V 2024-07-10 0.0 PT1H 3J83 2024-07-10 0.0 PT1H 3J85 2024-07-10 0.0 PT1H 3JBP 2024-07-10 0.0 PT1H 3JNR 2024-07-10 4900.0 PT1H 3JP6 2024-07-10 0.0 PT1H 3JP8 2024-07-10 0.0 PT1H 3JPA 2024-07-10 0.0 PT1H 3JPC 2024-07-10 0.0 PT1H 3JPE 2024-07-10 0.0 PT1H 3JPK 2024-07-10 0.0 PT1H 3JPM 2024-07-10 0.0 PT1H 3JQA 2024-07-10 0.0 PT1H 3JQC 2024-07-10 0.0 PT1H 3JQE 2024-07-10 0.0 PT1H 3K6T 2024-07-10 0.0 PT1H 3K6X 2024-07-10 0.0 PT1H 3K8A 2024-07-10 0.0 PT1H 3K8C 2024-07-10 0.0 PT1H 3K8E 2024-07-10 0.0 PT1H 3KJK 2024-07-10 0.0 PT1H 3KL4 2024-07-10 1000.0 PT1H 3KLQ 2024-07-10 4000.0 PT1H 3KOD 2024-07-10 0.0 PT1H 3KOL 2024-07-10 0.0 PT1H 3KVZ 2024-07-10 0.0 PT1H 3KXQ 2024-07-10 0.0 PT1H 3L9B 2024-07-10 0.0 PT1H 3LMH 2024-0

Como solo me interesa la data de plantas con un codigo especifico

In [0]:
dfResultsdfDespachoEnergia_filtered = dfResultsdfDespachoEnergia.filter(col('CodigoPlanta').isin(['ZPA2', 'ZPA3', 'ZPA4', 'ZPA5', 'GVIO', 'QUI1']))
display(dfResultsdfDespachoEnergia_filtered)

CodigoDuracion CodigoPlanta Fecha Compromiso PT1H GVIO 2024-07-10 60000.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 0.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 0.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 0.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 0.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 0.0 PT1H QUI1 2024-07-10 78000.0 PT1H GVIO 2024-07-10 0.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 0.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 0.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 0.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 490430.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 485840.0 PT1H QUI1 2024-07-10 78000.0 PT1H GVIO 2024-07-10 737330.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H ZPA2 2024-07-10 18000.0 PT1H ZPA3 2024-07-10 33000.0 PT1H ZPA4 2024-07-10 33000.0 PT1H ZPA5 2024-07-10 33000.0 PT1H GVIO 2024-07-10 1220000.0 PT1H QUI1 2024-07-10 340000.0 PT1H ZPA2 2024-07-10 26000.0 PT1H ZPA3 2024-07-10 33000.0 PT1H ZPA4 2024-07-10 33000.0 PT1H ZPA5 2024-07-10 33000.0 PT1H GVIO 2024-07-10 1220000.0 PT1H QUI1 2024-07-10 340000.0 PT1H ZPA2 2024-07-10 26000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 1220000.0 PT1H QUI1 2024-07-10 168290.0 PT1H ZPA2 2024-07-10 26000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 230590.0 PT1H QUI1 2024-07-10 78000.0 PT1H ZPA2 2024-07-10 17000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10 31000.0 PT1H ZPA5 2024-07-10 31000.0 PT1H GVIO 2024-07-10 1064890.0 PT1H QUI1 2024-07-10 78000.0 PT1H GVIO 2024-07-10 1220000.0 PT1H QUI1 2024-07-10 78000.0 PT1H GVIO 2024-07-10 1220000.0 PT1H QUI1 2024-07-10 164970.0 PT1H GVIO 2024-07-10 1220000.0 PT1H QUI1 2024-07-10 205710.0 PT1H GVIO 2024-07-10 1220000.0 PT1H QUI1 2024-07-10 340000.0 PT1H GVIO 2024-07-10 854640.0 PT1H ZPA2 2024-07-10 26000.0 PT1H ZPA3 2024-07-10 31000.0 PT1H ZPA4 2024-07-10

In [0]:
dfResultsdfDespachoEnergia_filtered.createOrReplaceTempView("Despacho")

In [0]:
dfDespacho_sumado = spark.sql("""
                                SELECT     
                                            CodigoPlanta,
                                            Fecha,
                                            sum(Compromiso) As suma_compromiso
                                FROM Despacho
                                GROUP BY CodigoPlanta, Fecha
                              """)

In [0]:
display(dfDespacho_sumado)

CodigoPlanta Fecha suma_compromiso ZPA3 2024-07-10 748000.0 ZPA5 2024-07-10 748000.0 ZPA2 2024-07-10 454000.0 QUI1 2024-07-10 2962970.0 ZPA4 2024-07-10 748000.0 GVIO 2024-07-10 1.272416E7

In [0]:
#Vamos a traer de nuevo nuestro dataframe inicial que proviene de la data de Excel
display(dfCapacidad_spark)

FECHA PLANTA GENERADOR CAPACIDAD (Kwh) CODIGO 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 20834 ZPA2 2024-07-10 TERMOZIPA 2 21626 ZPA2 2024-07-10 TERMOZIPA 2 26030 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 26294 ZPA2 2024-07-10 TERMOZIPA 2 28810 ZPA2 2024-07-10 TERMOZIPA 2 1422 ZPA2 2024-07-10 TERMOZIPA 2 32084 ZPA2 2024-07-10 TERMOZIPA 2 30188 ZPA2 2024-07-10 TERMOZIPA 2 29488 ZPA2 2024-07-10 TERMOZIPA 2 2944 ZPA2 2024-07-10 TERMOZIPA 2 33000 ZPA2 2024-07-10 TERMOZIPA 2 6986 ZPA2 2024-07-10 TERMOZIPA 3 27042 ZPA3 2024-07-10 TERMOZIPA 3 27012 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 28792 ZPA3 2024-07-10 TERMOZIPA 3 21734 ZPA3 2024-07-10 TERMOZIPA 3 2092 ZPA3 2024-07-10 TERMOZIPA 3 2110 ZPA3 2024-07-10 TERMOZIPA 3 14744 ZPA3 2024-07-10 TERMOZIPA 3 10106 ZPA3 2024-07-10 TERMOZIPA 3 24798 ZPA3 2024-07-10 TERMOZIPA 3 5394 ZPA3 2024-07-10 TERMOZIPA 3 16960 ZPA3 2024-07-10 TERMOZIPA 3 6788 ZPA3 2024-07-10 TERMOZIPA 3 21412 ZPA3 2024-07-10 TERMOZIPA 3 24676 ZPA3 2024-07-10 TERMOZIPA 3 21266 ZPA3 2024-07-10 TERMOZIPA 3 33000 ZPA3 2024-07-10 TERMOZIPA 3 904 ZPA3 2024-07-10 TERMOZIPA 3 11280 ZPA3 2024-07-10 TERMOZIPA 3 2238 ZPA3 2024-07-10 TERMOZIPA 4 17420 ZPA4 2024-07-10 TERMOZIPA 4 9402 ZPA4 2024-07-10 TERMOZIPA 4 29336 ZPA4 2024-07-10 TERMOZIPA 4 27208 ZPA4 2024-07-10 TERMOZIPA 4 4940 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 15428 ZPA4 2024-07-10 TERMOZIPA 4 16152 ZPA4 2024-07-10 TERMOZIPA 4 30120 ZPA4 2024-07-10 TERMOZIPA 4 7060 ZPA4 2024-07-10 TERMOZIPA 4 5360 ZPA4 2024-07-10 TERMOZIPA 4 27446 ZPA4 2024-07-10 TERMOZIPA 4 25728 ZPA4 2024-07-10 TERMOZIPA 4 5008 ZPA4 2024-07-10 TERMOZIPA 4 27526 ZPA4 2024-07-10 TERMOZIPA 4 31298 ZPA4 2024-07-10 TERMOZIPA 4 31824 ZPA4 2024-07-10 TERMOZIPA 4 2432 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 4 33000 ZPA4 2024-07-10 TERMOZIPA 5 852 ZPA5 2024-07-10 TERMOZIPA 5 19352 ZPA5 2024-07-10 TERMOZIPA 5 31480 ZPA5 2024-07-10 TERMOZIPA 5 3022 ZPA5 2024-07-10 TERMOZIPA 5 6278 ZPA5 2024-07-10 TERMOZIPA 5 22228 ZPA5 2024-07-10 TERMOZIPA 5 24230 ZPA5 2024-07-10 TERMOZIPA 5 24926 ZPA5 2024-07-10 TERMOZIPA 5 2304 ZPA5 2024-07-10 TERMOZIPA 5 23404 ZPA5 2024-07-10 TERMOZIPA 5 5666 ZPA5 2024-07-10 TERMOZIPA 5 19354 ZPA5 2024-07-10 TERMOZIPA 5 8372 ZPA5 2024-07-10 TERMOZIPA 5 13564 ZPA5 2024-07-10 TERMOZIPA 5 3806 ZPA5 2024-07-10 TERMOZIPA 5 32940 ZPA5 2024-07-10 TERMOZIPA 5 27364 ZPA5 2024-07-10 TERMOZIPA 5 7164 ZPA5 2024-07-10 TERMOZIPA 5 22170 ZPA5 2024-07-10 TERMOZIPA 5 15448 ZPA5 2024-07-10 TERMOZIPA 5 24080 ZPA5 2024-07-10 TERMOZIPA 5 17704 ZPA5 2024-07-10 TERMOZIPA 5 16420 ZPA5 2024-07-10 TERMOZIPA 5 13812 ZPA5 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1161384 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 441756 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 353958 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 907200 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1150828 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 1200000 GVIO 2024-07-10 GUAVIO 1 199938 GVIO 2024-07-10 GUAVIO 1 645326 GVIO 2024-07-10 GUAVIO 1 1200000

In [0]:
dfCapacidad_spark.createOrReplaceTempView("Capacidad_")

In [0]:
dfCapacidad_spark_grouped = spark.sql("""
    SELECT 
        CODIGO AS CodigoPlanta,
        FECHA AS Fecha,
        SUM(`CAPACIDAD (Kwh)`) AS suma_capacidad
    FROM 
        Capacidad_
    GROUP BY 
        CODIGO, FECHA
""")
display(dfCapacidad_spark_grouped)

CodigoPlanta Fecha suma_capacidad ZPA2 2024-07-10 655706 ZPA3 2024-07-10 467348 ZPA4 2024-07-10 544688 ZPA5 2024-07-10 385940 GVIO 2024-07-10 24230440 QUI1 2024-07-10 6570384

In [0]:
dfCapacidad_spark_grouped.createOrReplaceTempView("Capacidad_agrupada")
dfDespacho_sumado.createOrReplaceTempView("Despacho_agrupado")

In [0]:
#Vamos a unir dfCapacidad_spark_grouped con dfDespacho_sumado basado en CodigoPlanta, solamente nos interesa los valores que coincidan en codigoPlanta por esto hacemos un inner join
df_joined = spark.sql("""
                        SELECT  ca.Fecha,
                                da.CodigoPlanta,
                                ca.suma_capacidad AS capacidad,
                                da.suma_compromiso AS compromiso

                        FROM
                            Capacidad_agrupada ca
                        INNER JOIN
                            Despacho_agrupado da
                        ON
                            ca.CodigoPlanta == da.CodigoPlanta
                      """)
display(df_joined)

Fecha CodigoPlanta capacidad compromiso 2024-07-10 ZPA3 467348 748000.0 2024-07-10 ZPA5 385940 748000.0 2024-07-10 ZPA2 655706 454000.0 2024-07-10 QUI1 6570384 2962970.0 2024-07-10 ZPA4 544688 748000.0 2024-07-10 GVIO 24230440 1.272416E7

In [0]:
df_joined = df_joined.withColumn("capacidad", col("capacidad").cast("double"))
display(df_joined)

Fecha CodigoPlanta capacidad compromiso 2024-07-10 ZPA3 467348.0 748000.0 2024-07-10 ZPA5 385940.0 748000.0 2024-07-10 ZPA2 655706.0 454000.0 2024-07-10 QUI1 6570384.0 2962970.0 2024-07-10 ZPA4 544688.0 748000.0 2024-07-10 GVIO 2.423044E7 1.272416E7

In [0]:
#Ahora si vamos a calcular la diferencia entre mi compromiso y mi capacidad -> Balance
df_balance_calculado = df_joined.withColumn("Balance", col("capacidad") - col("compromiso"))
display(df_balance_calculado)

Fecha CodigoPlanta capacidad compromiso Balance 2024-07-10 ZPA3 467348.0 748000.0 -280652.0 2024-07-10 ZPA5 385940.0 748000.0 -362060.0 2024-07-10 ZPA2 655706.0 454000.0 201706.0 2024-07-10 QUI1 6570384.0 2962970.0 3607414.0 2024-07-10 ZPA4 544688.0 748000.0 -203312.0 2024-07-10 GVIO 2.423044E7 1.272416E7 1.150628E7

Debido a que el proceso que estamos realizando es un proceso diario, solamente estamos interesado en el precio de la energia para ese dia 
asi que unicamente consideraremos para el dia vigente el valor  en codigoVariable asociado a PPBOGReal y Version TXR

Esto nos dara el valor por el cual debemos multiplicar nuestro balance para obtener el Compromisos_MCOP en miles de millones de pesos


In [0]:
factor_multiplicador = spark.sql("""
                                 SELECT Valor FROM
                                 Precios
                                 WHERE
                                    codigoVariable == 'PPBOGReal' AND
                                    Version == 'TXR'              AND
                                    Fecha == '2024-07-10'
                                 """).first()

factor_multiplicador = factor_multiplicador['Valor']

In [0]:
df_balance_calculado = df_balance_calculado.withColumn("Compromisos_MCOP", (col("Balance")* factor_multiplicador)/1000)
display(df_balance_calculado)

Fecha CodigoPlanta capacidad compromiso Balance Compromisos_MCOP 2024-07-10 ZPA3 467348.0 748000.0 -280652.0 -61675.0170424 2024-07-10 ZPA5 385940.0 748000.0 -362060.0 -79564.929772 2024-07-10 ZPA2 655706.0 454000.0 201706.0 44326.144077200006 2024-07-10 QUI1 6570384.0 2962970.0 3607414.0 792751.5924668 2024-07-10 ZPA4 544688.0 748000.0 -203312.0 -44679.0725344 2024-07-10 GVIO 2.423044E7 1.272416E7 1.150628E7 2528576.368936

In [0]:
from pyspark.sql.types import IntegerType
from pyspark.sql.functions import col

df_balance_calculado = df_balance_calculado.withColumn(
    "Compromisos_MCOP",
    ((col("Balance") * factor_multiplicador) / 1000).cast(IntegerType())  # Convierte a entero
)
display(df_balance_calculado)


Fecha CodigoPlanta capacidad compromiso Balance Compromisos_MCOP 2024-07-10 ZPA2 655706.0 454000.0 201706.0 44326 2024-07-10 ZPA3 467348.0 748000.0 -280652.0 -61675 2024-07-10 ZPA4 544688.0 748000.0 -203312.0 -44679 2024-07-10 ZPA5 385940.0 748000.0 -362060.0 -79564 2024-07-10 GVIO 2.423044E7 1.272416E7 1.150628E7 2528576 2024-07-10 QUI1 6570384.0 2962970.0 3607414.0 792751

In [0]:
informe_balance_energia = df_balance_calculado.withColumn("Accion", when(col("Balance") < 0 , "Comprar energia").otherwise("Vender energia"))

In [0]:
display(informe_balance_energia)

Fecha CodigoPlanta capacidad compromiso Balance Compromisos_MCOP Accion 2024-07-10 ZPA3 467348.0 748000.0 -280652.0 -61675 Comprar energia 2024-07-10 ZPA5 385940.0 748000.0 -362060.0 -79564 Comprar energia 2024-07-10 ZPA2 655706.0 454000.0 201706.0 44326 Vender energia 2024-07-10 QUI1 6570384.0 2962970.0 3607414.0 792751 Vender energia 2024-07-10 ZPA4 544688.0 748000.0 -203312.0 -44679 Comprar energia 2024-07-10 GVIO 2.423044E7 1.272416E7 1.150628E7 2528576 Vender energia

In [0]:
1==1
print(True)

True
